---

# S03E06 : Functions & decorators - functools module

Cyril Desjouy

---



## 1. Introspection

Introspection is the ability of an object to know its own attributes. Introspection is very powerful under Python. For example, a function knows its name and documentation, among other things. Let's take the example of the built-in `len` function:

```python
>> len.__name__
'len'
>> len.__doc__          # Equivalent to help(len)
Return the number of items in a container.
```

## 2. The decorators

<div class="alert alert-block alert-info">
Take the example of the previous notebook and look at the attributes <code>__name__</code> and <code>__doc__</code> of the function <code>stuff</code> decorated.
</div>

In [2]:
def prettier(func):
    def wrapper(*args, **kwargs):
        result = func(*args, **kwargs)
        print('.oOO Processing OOo.'.center(80))
        print(result)
        print('.oOO ~~~Done~~~ OOo.'.center(80))
        return result                            # Return func(*args, **kwargs)
    return wrapper

@prettier
def stuff(task, like_a=''):
    return f'Doing {task} like a {like_a}'.center(80)

You will have noticed that after being decorated, `stuff` lost its attributes `__name__` and `__doc__` which were replaced by those of `wrapper`. To fix this problem, decorators can use the `wraps` decorator provided by the standard `functools` module. This decorator allows in particular to preserve the original attributes of the decorated function:

<div class="alert alert-block alert-info">
What are now the values of the attributes <code>__name__</code> and <code>__doc__</code> of the function <code>stuff</code> decorated.
</div>

**Note:** *`wrap` is a comfort function to invoke `update_wrapper` as a decorator. If you need to use `wrap` in a functional form, you should use `update_wrapper`:*
```Python
update_wrapper(wrapper, wrapped) # in our case: update_wrapper(wrapper, func)
```

In [ ]:
import functools

def prettier(func):
    @functools.wraps(func)
    def wrapper(*args, **kwargs):
        result = func(*args, **kwargs)
        print('.oOO Processing OOo.'.center(80))
        print(result)
        print('.oOO ~~~Done~~~ OOo.'.center(80))
        return result                            # Return func(*args, **kwargs)
    return wrapper

@prettier
def stuff(task, like_a=''):
    """Do Stuff."""
    return f'Doing {task} like a {like_a}'.center(80)

## 3. The functools module in more detail

One of Python's greatest strengths is that it provides tools for writing code that can be easily reused. We have already discussed this with the decorators. The standard module `functools` also provides tools to work with functions or other ***callable*** objects and to adapt or extend their functionality for reuse in other contexts.

Let us mention in particular:

* `partial` allowing to create `partial functions`.
* `singledispatch` allowing to create `generic functions`.

This section provides an overview of the possibilities offered by `functools`.

### 3.1. The ***partial functions***

***partial functions*** are functions that reproduce the behavior of a basic function by *"freezing "* some of its arguments. The following example illustrates this:

```python
from functools import partial

def repeat(char, n):
    print(f'{char*n:^80}')

stars = partial(repeat, char='*')
pipes = partial(repeat, char='|')
let_v = partial(repeat, char='v')
```

The three functions `stars`, `pipes` and `let_v` created through `partial` are thus `repeat` specializations.

<div class="alert alert-block alert-info">
Implement these <b><i>>partial functions</i></b> and perform the following tests:
</div>

```python
stars(n=20)
pipes(n=10)
let_v(n=5)
```

These ***partial functions*** can be used as completely independent functions. However, they always keep a record of the functions used to create them:
```Python
>> stars.func
<function __main__.repeat(char, n)>
>> stars.keywords
{'char':'*'}
```

**Note:** *This concept of ***partial function*** also extends to methods since Python 3.4, so it is a question of using ***partialmethod*** instead of ***partial***.*

### 3.2. The ***Generic functions***

A ***generic function*** is a function that offers different implementations in the same ***scope*** depending on the type of arguments. This type of implementation is possible thanks to the `@singledispatch` decorator provided by the `functools` module since Python 3.4.

A ***generic function*** is composed of several functions implementing the same operation for different types. A distribution algorithm (***dispatch***) then determines which implementation to use according to the type of arguments. Using the `@singledispatch` decorator, the distribution is chosen from the type of a **unique** argument, hence the name ***single dispatch***.

To create a ***generic function***:

* Decorate a basic function with `@singledispatch`.
* Implement alternative functions by decorating them with `@function_name.register(type)` where `function_name` is the name of the base function and `type` is the type of the first argument of this function. It is possible to stack the decorators.
* The name of the alternative implementations must be `_` if you only want one generic function. However, it is possible to give a name to alternative implementations. In this case, you will have the possibility to call them directly.

>**Note 1:** *If you use the **annotation type**, it is not necessary to specify the type to be `registered`:*
>```python
@display.register
def _(obj:list):
    strings =[str(i) for i in obj]
    print(f "List with elements {', '.join(strings)}")
```
**Note 2:** *`register()` can be used in its functional form to be applied to `lambda` functions for example:*
>python
display.register(tuple, lambda obj: print('tuple:', obj))
```
**Note 3:** *This concept of ***generic function*** also extends to methods since Python 3.8. It is then a question of using ***singledispatchmethod*** instead of ***singledispatch***.*


For example:

In [ ]:
from functools import singledispatch
  
@singledispatch
def display(obj):
    raise NotImplementedError('Unsupported type')
 
@display.register(int)
@display.register(float)
def _(obj):
    print(f'Numerical object with value {obj}')

@display.register(list)
def _(obj):
    strings = [str(i) for i in obj]
    print(f"List with elements {', '.join(strings)}")

<div class="alert alert-block alert-info">
Run the following tests to understand how <code>singledispatch</code> works:
</div>

```python
display(1)
display(2.1)
display([1, 2])
display((1, 2))
```

### 3.3. The `reduce` function

The `reduce` function of the `functools` module is often studied in parallel with `map` and `filter` functions because it follows the same logic.

* `map` applies a function to all elements of a sequence. It returns an iterator.
* `filter` creates an iterator containing all the elements of a sequence for which the function returned `True`.
* `reduce` applies a two-argument function cumulatively to all elements of a sequence.

For example:
```python
>> list(map((lambda x: x**2), [1, 2, 3, 4]))
[1, 4, 9, 16]
>> list(filter((lambda x: x>2), [1, 2, 3, 4]))
[3, 4]
>> functools.reduce((lambda x, y: x*y), [1, 2, 3, 4])
24
```

This last example comes back to:
```python
product = 1
for i in [1, 2, 3, 4]:
    product = product * i
```

The operation of `reduce` is as follows:

* the function is applied to the first two elements of the sequence,
* then the function is applied to the previous result and the third element, 
* then this method is applied to the following elements,
* finally, the final result is returned.


>**Note:** *The `reduction` function of `functools` is similar to the `accumulate` function of `itertools` with the following exceptions:*
>
>* The `reduce` stores the intermediate results and returns only the final result. 
* `accumulate` returns a list containing the intermediate results. The last item in the list is the final result.
* `reduce(function, sequence)` vs. `accumulate(sequence, function)`
* `accumulates` seems faster:
>
>    * `%timeit functools.reduce((lambda x, y: x*y),[1, 2, 3, 4])` => 553ns
>    * `%timeit itertools.accumulate([1, 2, 3, 3, 4], (lambda x, y: x*y))` => 334ns


### 3.4. Automation of comparisons

The `functools` module also provides a tool to automate the creation of comparison functions. This is the `@total_ordering` decorator. Two conditions must be met for automation to occur:

* At least one comparison operation must be defined among `__le__`, `__lt__`, `__gt__` or `__ge__`.
* The method `__eq__` is required.

For example:

In [ ]:
import functools

@functools.total_ordering
class Int:
    def __init__(self, value):
        self.value = value
    def __eq__(self, other):
        return self.value == other.value
    def __gt__(self, other):
        return self.value > other.value

All comparison operations are then available for `Int` instances:
```python
>> Int(1) <= Int(2)
True
```

<div class="alert alert-block alert-info">
Test the other comparison operations. </div>

### 3.5. Caching

The `functools` module also provides two decorators used to optimize code parts:

* `cached_property` (Python 3.8): Transforms a class method into a `property' (see the corresponding notebook in the ***Classes & OOP*** part) whose value is calculated only once and cached throughout the lifetime of the instance. This decorator is used for ***properties*** whose calculation is expensive.

* `lru_cache(maxsize)` (Python 3.2): Envelops a function with callable storage that allows you to record up to the most recent `maxsize` calls. This decorator saves time when a costly or I/O-related function is called periodically with the same arguments.

## References

* [Python.org - functools](https://docs.python.org/3.7/library/functools.html)
* [Journaldev.com - functools](https://www.journaldev.com/17550/python-functools)